## Домашнее задание 3 (до 09/3/17). keras
### Коломиец Андрей, Иад-6

In [1]:
import pandas as pd
import numpy as np
import math

In [2]:
male = pd.read_csv('hw3_data/male.txt',header=None,names=['Name'],dtype={'Name':str})
female = pd.read_csv('hw3_data/female.txt',header=None,names=['Name'],dtype={'Name':str})
female.head()

Name
0  Abagael
1  Abagail
2     Abbe
3    Abbey
4     Abbi

### Предварительная обработка данных

### 1) удалите неоднозначные имена (те имена, которые являются и мужскими, и женскими одновременно), если такие есть

In [3]:
len(male),len(female)

(2943, 5001)

In [4]:
toDelete = []
mal = [x[1] for x in male.itertuples()]
for f in female.itertuples():
    if f[1] in mal:
        toDelete.append(f[1])
toDelete[:5], len(toDelete)

(['Abbey', 'Abbie', 'Abby', 'Addie', 'Adrian'], 365)

In [5]:
for f in toDelete:
    female = female[female.Name!=f]
    male = male[male.Name!=f]
len(male),len(female)

(2578, 4636)

Приводить слова к lowcase не считаю стоящим, заглавная буква несет информацию. Также, много схожих имен начинаются одиноково, и не лишним будет различать с окончаниями, напр.: (An)n, (An)na, (An)astacia vs Sebasti(an), Dori(an) 

### 2) создайте тестовое множество по следующему принципу: 20% от общего количества имен на каждую букву (т.е. 20% от имен на букву А, 20% имен на букву B, и.т.д.).

In [7]:
# Создадим целевой признак
female['y'] = 0
male['y'] = 1
# При удалении неоднозначных имен возникли пропуски.
male = male.dropna()
# Для конкатенации датафреймов, нужно переопределить индексы
male.index = range(len(male))
female = female.dropna()
female.index = range(len(male),len(female)+len(male))

In [8]:
df = pd.concat([male, female])

In [9]:
# Для разделения на тестовое и обучающее множества
df['letter'] = df['Name'].apply(lambda x:x[0])

In [10]:
from sklearn.cross_validation import train_test_split
train = df[df.Name==None]
test = df[df.Name==None]
for letter, words in df.groupby(['letter']):
    tr, te = train_test_split(words, test_size=0.2)
    train = pd.concat([train, tr])
    test = pd.concat([test, te])

C:\Users\Computer\Anaconda3\lib\site-packages\sklearn\cross_validation.py:44: DeprecationWarning: This module was deprecated in version 0.18 in favor of the model_selection module into which all the refactored classes and functions are moved. Also note that the interface of the new CV iterators are different from that of this module. This module will be removed in 0.20.
  "This module will be removed in 0.20.", DeprecationWarning)


In [11]:
len(train),len(test)

(5757, 1457)

### Используйте метод наивного Байеса для классификации имен: в качестве признаков используйте символьные n-граммы. Сравните результаты, получаемые при разных n = 2;3;4 по F - мере и аккуратности.

In [12]:
from nltk import NaiveBayesClassifier
from nltk.util import ngrams
from sklearn.metrics import accuracy_score
from sklearn.metrics import f1_score

In [13]:
def get_ngram(name, n):
    return tuple(ngrams(name, n))
# Проверка извлечения н-граммы
for n in get_ngram('Abbie',3):
    print(n)

('A', 'b', 'b')
('b', 'b', 'i')
('b', 'i', 'e')


In [14]:
# Возвращает множество всех возможных нграмм в датасете
def all_the_ngrams(dfs,n):
    allthe = set()
    for df in dfs:
        for name in df.Name:
            allthe.update(get_ngram(name,n))
    return allthe

In [15]:
# Возвращает словарь признаков: какие нграммы из датасета встречаются в слове
def get_dict(namegrams,allthe):
    return {ngram:ngram in namegrams
            for ngram in allthe}
# Возвращает тестовое множество в формате, доступном для предсказания
def get_testable(dfXY,allthe,n):
    return [get_dict(get_ngram(name,n),allthe) for name in dfXY.Name]
# Возвращает обучающее множество и целевые признаки в формате, доступном для обучения
def get_trainable(dfXY,allthe,n):
    return [(get_dict(get_ngram(name,n),allthe),y) for name,y in zip(dfXY.Name,dfXY.y)]

In [16]:
# Всевозможные 2-3-4-граммы
ALL_GRAMS2 = all_the_ngrams([train,test],2)
ALL_GRAMS3 = all_the_ngrams([train,test],3)
ALL_GRAMS4 = all_the_ngrams([train,test],4)

C:\Users\Computer\Anaconda3\lib\site-packages\ipykernel\__main__.py:2: DeprecationWarning: generator 'ngrams' raised StopIteration
  from ipykernel import kernelapp as app


In [17]:
ALL_GRAMS = {2:ALL_GRAMS2,3:ALL_GRAMS3,4:ALL_GRAMS4}

In [20]:
import timeit

In [22]:
%%time
preds = []
fscores = []
accs = []

for N in (2,3,4):
    trainable = get_trainable(train,ALL_GRAMS[N],N)
    testable = get_testable(test,ALL_GRAMS[N],N)
    clf = NaiveBayesClassifier.train(trainable)
    pred = clf.classify_many(testable)
    fscore = f1_score(test.y,pred)
    acc = accuracy_score(test.y,pred)
    preds.append(pred)
    fscores.append(fscore)
    accs.append(acc)
    print('N={}, F={}, Acc={}'.format(N,fscore,acc))

N=2, F=0.672097759674, Acc=0.778997940975
N=3, F=0.738430583501, Acc=0.821551132464
N=4, F=0.665943600868, Acc=0.78860672615
Wall time: 5min 26s


Наивный Байесовский классификатор на основе н-грамм показал приемлемый результат. Лучшая метрика достигнута при n=3. Логично, что при увеличении n, слова почти не будут иметь совпадающих признаков, а при уменьшении n, связь сводится к наличию/отсутствию букв в имени.

### В каких случаях метод ошибается?

In [23]:
pred = preds[1]

In [24]:
failures = set([name if pr!=tr else None for pr,tr,name in zip(pred,test.y,test.Name)])
failures, len(failures)

({None,
  'Ace',
  'Aditya',
  'Adriaens',
  'Alayne',
  'Alic',
  'Allen',
  'Alley',
  'Allsun',
  'Alvin',
  'Ambur',
  'Antonella',
  'Aphrodite',
  'Arie',
  'Ashish',
  'Augusta',
  'Austen',
  'Averyl',
  'Avi',
  'Bathsheba',
  'Beck',
  'Bela',
  'Bertha',
  'Blanca',
  'Boris',
  'Boyce',
  'Brande',
  'Carlos',
  'Charles',
  'Charmain',
  'Chen',
  'Cheslie',
  'Chet',
  'Chev',
  'Chevalier',
  'Conchita',
  'Connolly',
  'Constantin',
  'Courtenay',
  'Damien',
  'Daren',
  'Darien',
  'Darrell',
  'Daryle',
  'Delmar',
  'Denis',
  'Dino',
  'Domenic',
  'Domenico',
  'Dominic',
  'Dominick',
  'Dru',
  'Ealasaid',
  'Earl',
  'Earle',
  'Ebony',
  'Ed',
  'Eddi',
  'Effie',
  'Elke',
  'Ely',
  'Emmett',
  'Emmit',
  'Enid',
  'Erl',
  'Ernie',
  'Ester',
  'Eugene',
  'Eustace',
  'Fabian',
  'Fabio',
  'Federica',
  'Felicio',
  'Feodora',
  'Finn',
  'Floyd',
  'Flynn',
  'Frances',
  'Francesca',
  'Franciska',
  'Francois',
  'Freddi',
  'Friederike',
  'Gabriello'

Примечательных закономерностей не выявлено

### Используйте сеть с двумя слоями LSTM для определения пола. Представление имени для классификации в этом случае: 2-мерный бинарный вектор количество букв в алфавите  максимальная длина имени. Обозначим его через x. Если первая буква имени a, то x[1][1] = 1, если вторая – b, тоx[2][1] = 1.  Не забудьтепро регуляризацию нейронной сети дропаутами. 

In [21]:
maxlen = df.Name.apply(lambda x:len(x)).max()
maxlen # макс длина слова

15

In [22]:
alphabet = set()
for name in df.Name:
    alphabet.update(set(''.join(name)))
alphabet = sorted(list(alphabet))
alphalen = len(alphabet) # количество символов в именах. 
alphabet, len(alphabet)

([' ',
  "'",
  '-',
  'A',
  'B',
  'C',
  'D',
  'E',
  'F',
  'G',
  'H',
  'I',
  'J',
  'K',
  'L',
  'M',
  'N',
  'O',
  'P',
  'Q',
  'R',
  'S',
  'T',
  'U',
  'V',
  'W',
  'X',
  'Y',
  'Z',
  'a',
  'b',
  'c',
  'd',
  'e',
  'f',
  'g',
  'h',
  'i',
  'j',
  'k',
  'l',
  'm',
  'n',
  'o',
  'p',
  'q',
  'r',
  's',
  't',
  'u',
  'v',
  'w',
  'x',
  'y',
  'z'],
 55)

In [23]:
# Возвращает векторное представление имени
def to_arr(name, arr=None, first=0):
    if arr==None:
        arr = np.zeros((1,maxlen,alphalen),dtype=np.bool)
    nameLen = len(name)
    for i in range(nameLen):
        for j in range(alphalen):
            if name[i]==alphabet[j]:
                arr[first,i,j] = 1
    return arr
# Возвращает векторное представление набора имен, который можно использовать в модели
def to_arrs(names):
    arr = np.zeros((len(names),maxlen,alphalen),dtype=np.bool)
    i = 0
    for name in names:
        to_arr(name,arr,i)
        i+=1
    return arr
# Возвращает векторное представление вектора целевого признака, который можно использовать в модели
def to_y(names,y):
    arr = np.zeros((len(names),2))
    for (i,name),(j,sex) in zip(enumerate(names),enumerate(y)):
        arr[i,sex] = 1
    return arr

In [24]:
from keras.models import Sequential
from keras.layers.core import Dense, Activation, Dropout
from keras.layers.recurrent import LSTM

Using Theano backend.


In [25]:
# Создает модель с заданными параметрами числа узлов и dropout
def get_model(n,dropout):
    model = Sequential()
    model.add(LSTM(n,return_sequences=True,input_shape=(maxlen,alphalen)))
    model.add(Dropout(dropout))
    model.add(LSTM(n,return_sequences=False))
    model.add(Dropout(dropout))
    model.add(Dense(2))
    model.add(Activation('softmax'))
    
    model.compile(metrics=['accuracy','fmeasure'],optimizer='rmsprop',loss='binary_crossentropy')
    return model

In [32]:
# Изучим влияние гиперпараметров
model_preds = []
model_accs = []
model_fs = []
train_arr = to_arrs(train.Name)
train_arrY = to_y(train.Name,train.y)
test_arr = to_arrs(test.Name)
i = 0
for N in (32,64):#,256): # 256 считает уже на порядок дольше
    for DROPOUT in (0.1,0.2,0.5):#,0.2,0.4):
        for BATCH in (64,32):
            for NB in (10,15,25):
                model = get_model(N,DROPOUT)
                model.fit(train_arr,train_arrY,batch_size=BATCH,nb_epoch=NB)
                pred = model.predict_classes(test_arr)
                model_preds.append(pred)                
                fscore = f1_score(test.y,pred)
                acc = accuracy_score(test.y,pred)
                model_fs.append(fscore)
                model_accs.append(acc)
                print()
                print('{}:N={},D={},B={},N={} F={}, Acc={}'.format(i,N,DROPOUT,BATCH,NB,fscore,acc))
                i+=1

C:\Users\Computer\Anaconda3\lib\site-packages\ipykernel\__main__.py:2: FutureWarning: comparison to `None` will result in an elementwise object comparison in the future.
  from ipykernel import kernelapp as app


Epoch 1/10
5757/5757 [==============================] - 4s - loss: 0.5757 - acc: 0.7014 - fmeasure: 0.7014     

KeyboardInterrupt: 

In [35]:
model_accs

[0.80645161290322576,
 0.81880576527110505,
 0.83390528483184623,
 0.80096087851750175,
 0.82086479066575158,
 0.8407687028140014,
 0.81262868908716546,
 0.82155113246396705,
 0.82566918325326011,
 0.81331503088538093,
 0.82772820864790664,
 0.84420041180507888,
 0.80507892930679481,
 0.8318462594371997,
 0.83733699382292381,
 0.81331503088538093,
 0.82841455044612222,
 0.8407687028140014,
 0.82017844886753599,
 0.82772820864790664,
 0.84145504461221687,
 0.82429649965682905,
 0.84420041180507888,
 0.84969114619080299,
 0.81811942347288946,
 0.82635552505147558,
 0.84763212079615646,
 0.81331503088538093,
 0.85655456417295817,
 0.85380919698009605,
 0.81674673987645852,
 0.82017844886753599,
 0.85037748798901858,
 0.83321894303363075,
 0.83665065202470834,
 0.86890871654083734,
 0.83459162663006181]

In [36]:
model_fs

[0.72621359223300974,
 0.74664107485604603,
 0.7695238095238095,
 0.75000000000000011,
 0.72263549415515405,
 0.76753507014028044,
 0.73156342182890866,
 0.758812615955473,
 0.73814432989690715,
 0.73122529644268774,
 0.75654704170708043,
 0.79641255605381167,
 0.70230607966457015,
 0.76003917727717929,
 0.77363896848137548,
 0.71002132196162038,
 0.75149105367793234,
 0.76082474226804131,
 0.72877846790890277,
 0.7497507477567299,
 0.78020932445290192,
 0.7424547283702212,
 0.79193400549954174,
 0.80180995475113126,
 0.75164011246485463,
 0.76595744680851063,
 0.78192534381139489,
 0.76140350877192986,
 0.79728419010669249,
 0.79617224880382775,
 0.7337986041874377,
 0.77057793345008763,
 0.787109375,
 0.7557788944723618,
 0.75813008130081283,
 0.8186134852801521,
 0.76209279368213234]

### Влияние гиперпараметров модели на результат:

1) Не наблюдается деградация итоговой метрики при увеличении числа итераций:

In [41]:
[(a,b,c) for a,b,c in zip(model_accs[::3],model_accs[1::3],model_accs[2::3])]
#NB=10                   NB=15                  NB=25

[(0.80645161290322576, 0.81880576527110505, 0.83390528483184623),
 (0.80096087851750175, 0.82086479066575158, 0.8407687028140014),
 (0.81262868908716546, 0.82155113246396705, 0.82566918325326011),
 (0.81331503088538093, 0.82772820864790664, 0.84420041180507888),
 (0.80507892930679481, 0.8318462594371997, 0.83733699382292381),
 (0.81331503088538093, 0.82841455044612222, 0.8407687028140014),
 (0.82017844886753599, 0.82772820864790664, 0.84145504461221687),
 (0.82429649965682905, 0.84420041180507888, 0.84969114619080299),
 (0.81811942347288946, 0.82635552505147558, 0.84763212079615646),
 (0.81331503088538093, 0.85655456417295817, 0.85380919698009605),
 (0.81674673987645852, 0.82017844886753599, 0.85037748798901858),
 (0.83321894303363075, 0.83665065202470834, 0.86890871654083734)]

In [48]:
predsN25 = model_accs[2::3]

2) Размер Batch влияет на результат, но не коррелирует с метрикой качества.

In [46]:
same_batch_in_row = [(a,b,c) for a,b,c in zip(model_accs[::3],model_accs[1::3],model_accs[2::3])]
[(a[i],b[i]) for a,b in zip(same_batch_in_row[::2],same_batch_in_row[1::2]) for i in range(3)]
#BatchSize=64,             BatchSize=32

[(0.80645161290322576, 0.80096087851750175),
 (0.81880576527110505, 0.82086479066575158),
 (0.83390528483184623, 0.8407687028140014),
 (0.81262868908716546, 0.81331503088538093),
 (0.82155113246396705, 0.82772820864790664),
 (0.82566918325326011, 0.84420041180507888),
 (0.80507892930679481, 0.81331503088538093),
 (0.8318462594371997, 0.82841455044612222),
 (0.83733699382292381, 0.8407687028140014),
 (0.82017844886753599, 0.82429649965682905),
 (0.82772820864790664, 0.84420041180507888),
 (0.84145504461221687, 0.84969114619080299),
 (0.81811942347288946, 0.81331503088538093),
 (0.82635552505147558, 0.85655456417295817),
 (0.84763212079615646, 0.85380919698009605),
 (0.81674673987645852, 0.83321894303363075),
 (0.82017844886753599, 0.83665065202470834),
 (0.85037748798901858, 0.86890871654083734)]

3) Dropout незначительно улучшает результат, причем максимальные метрики достигаются при dropout=0.5

In [55]:
best_for_dropout = [max(a,b) for a,b in zip(predsN25[::2],predsN25[1::2])]
[(a,b,c) for a,b,c in zip(best_for_dropout[::3],best_for_dropout[1::3],best_for_dropout[2::3])]
#Dropout = 0.1            Dropout = 0.2         Dropout = 0.5

[(0.8407687028140014, 0.84420041180507888, 0.8407687028140014),
 (0.84969114619080299, 0.85380919698009605, 0.86890871654083734)]

In [56]:
mean_for_dropout = [a+b for a,b in zip(predsN25[::2],predsN25[1::2])]
[(a,b,c) for a,b,c in zip(mean_for_dropout[::3],mean_for_dropout[1::3],mean_for_dropout[2::3])]
#Dropout = 0.1            Dropout = 0.2         Dropout = 0.5

[(1.6746739876458476, 1.6698695950583389, 1.6781056966369252),
 (1.6911461908030199, 1.7014413177762524, 1.719286204529856)]

4) Не наблюдается деградация итоговой метрики при увеличении числа узлов. На достижимых по времени числах узлов чем больше узлов, тем лучше результат. Время обучение сильно увеличивается при увеличении числа узлов

In [59]:
[(a,b) for a,b in zip(model_accs[:18],model_accs[18:])]
# N=32                  N=64

[(0.80645161290322576, 0.82017844886753599),
 (0.81880576527110505, 0.82772820864790664),
 (0.83390528483184623, 0.84145504461221687),
 (0.80096087851750175, 0.82429649965682905),
 (0.82086479066575158, 0.84420041180507888),
 (0.8407687028140014, 0.84969114619080299),
 (0.81262868908716546, 0.81811942347288946),
 (0.82155113246396705, 0.82635552505147558),
 (0.82566918325326011, 0.84763212079615646),
 (0.81331503088538093, 0.81331503088538093),
 (0.82772820864790664, 0.85655456417295817),
 (0.84420041180507888, 0.85380919698009605),
 (0.80507892930679481, 0.81674673987645852),
 (0.8318462594371997, 0.82017844886753599),
 (0.83733699382292381, 0.85037748798901858),
 (0.81331503088538093, 0.83321894303363075),
 (0.82841455044612222, 0.83665065202470834),
 (0.8407687028140014, 0.86890871654083734)]

5) Обучим модель на параметрах N=256, D=0.5, NB=25,Batch=16

In [60]:
model = get_model(256,0.5)
model.fit(train_arr,train_arrY,batch_size=16,nb_epoch=25)
pred = model.predict_classes(test_arr)
model_preds.append(pred)                
f256 = f1_score(test.y,pred)
acc256 = accuracy_score(test.y,pred)
print()
print('N=256,D=0.5,B=16,NB=25 F={}, Acc={}'.format(f256,acc256))

Epoch 1/25
5757/5757 [==============================] - 42s - loss: 0.5287 - acc: 0.7438 - fmeasure: 0.7438     

In [76]:
failures = list(set([name if pr!=tr else None for pr,tr,name in zip(pred,test.y,test.Name)]))
failures.remove(None)
failures.sort()
(failures, len(failures))

(['Abdel',
  'Abel',
  'Adnan',
  'Ag',
  'Aldis',
  'Alexander',
  'Alister',
  'Anatole',
  'Anatoly',
  'Andrey',
  'Andri',
  'Andromache',
  'Antoine',
  'Antone',
  'Anurag',
  'Ashby',
  'Ashish',
  'Avraham',
  'Baillie',
  'Barbabas',
  'Beck',
  'Beilul',
  'Bentley',
  'Berkie',
  'Blaine',
  'Boniface',
  'Brodie',
  'Bubba',
  'Buffy',
  'Burnaby',
  'Cain',
  'Cameron',
  'Carl',
  'Carter',
  'Christ',
  'Chrisy',
  'Clarke',
  'Cleland',
  'Clemente',
  'Clio',
  'Clive',
  'Conan',
  'Connor',
  'Conroy',
  'Corky',
  'Danie',
  'Darell',
  'Davie',
  'Denis',
  'Dennis',
  'Di',
  'Dickie',
  'Dino',
  'Donn',
  'Dorcas',
  'Earle',
  'Elijah',
  'Elroy',
  'Emory',
  'Erinn',
  'Ethelind',
  'Eudora',
  'Everett',
  'Farrand',
  'Ferdinand',
  'Flem',
  'Francois',
  'Frederik',
  'Galen',
  'Germain',
  'Glennis',
  'Glynn',
  'Grant',
  'Gredel',
  'Harlin',
  'Hedy',
  'Hester',
  'Hezekiah',
  'Ignace',
  'Inez',
  'Inger',
  'Isaak',
  'Isidora',
  'Izaak',
  'J

За редким исключением (напр., Dino), нейронная сеть и Байесовский классификатор ошибаются в разных именах

Нейронная сеть идентифицировала более глубокие связи между именами и целевым признаком (полом), нежели наивный Байесовский классификатор на основе n-грамм, в том числе поскольку анализ слов не ограничивался последовательностями подряд идущих букв.